In [1]:
import os

In [2]:
%pwd

'e:\\Risk-Analysis\\research'

In [3]:
os.chdir('../')

In [4]:
%pwd

'e:\\Risk-Analysis'

In [7]:
from pathlib import Path
from dataclasses import dataclass

@dataclass(frozen=True)
class Model_EvalConfig:
    model_eval : Path
    updated_model : Path
    transformation_dir:Path
    preprocessor_dir :Path



In [8]:
from src.Risk_Analysis.constants import config_file
from src.Risk_Analysis.constants import params_file
from src.Risk_Analysis.utils.common import real_yaml,create_directories

In [9]:
class Configuration:
    def __init__(self,config=config_file,params=params_file):
        self.config=real_yaml(config)
        self.params=real_yaml(params)
        create_directories([self.config.Artifacts])

    def get_model_evaluation(self)->Model_EvalConfig:
        
        evaluation=self.config.Model_Evaluation
        transformation=self.config.Data_Transformation

        create_directories([evaluation.model_eval])

        model_evaluation=Model_EvalConfig(
            model_eval=evaluation.model_eval,
            updated_model=evaluation.updated_model,
            transformation_dir=transformation.transformation_dir,
            preprocessor_dir =transformation.preprocessor_dir
           
        )
        return model_evaluation


In [10]:
from sklearn.metrics import accuracy_score,classification_report,confusion_matrix,recall_score
from src.Risk_Analysis.utils.common import load_object,save_oject
from sklearn.model_selection import GridSearchCV
from src.Risk_Analysis.components.data_transformation import DataTransformation


In [11]:
class Model_Eval:
    def __init__(self,config):
        self.config=config


    def model_eval(self,x_train,y_train):

        model=load_object('artifacts\model_trainer\model.pkl')

        cat_model=model

        params_grid = {'iterations': [100, 200, 300, 400, 500],
                       'learning_rate': [0.1, 0.2, 0.3, 0.4],
                       'max_depth': [1, 3, 4, 5]}
        grid_model=GridSearchCV(estimator=cat_model,param_grid=params_grid,cv=5,scoring='recall')

        grid_model.fit(x_train,y_train)

        return (grid_model.best_params_,cat_model)
    
    def updated_model(self,x_train,y_train,x_test,y_test):

        model_dict,cat_model=self.model_eval(x_train=x_train,y_train=y_train)

        updated_model=cat_model(iterations=model_dict['iterations'],learning_rate=model_dict['learning_rate'],
                                max_depth=model_dict['max_depth'])
        
        save_oject(self.config.updated_model,obj=updated_model)

        predict=updated_model.predict(x_test)

        r_score=recall_score(y_test,predict)
        a_score=accuracy_score(y_test,predict)
        return (r_score,a_score)

In [12]:
eval=Configuration()

config=eval.get_model_evaluation()


transformation=DataTransformation(config)
x_train,x_test,y_train,y_test=transformation.data_transformation_initiated()

model_evl=Model_Eval(config=config)

r_score,a_score=model_evl.updated_model(x_train=x_train,x_test=x_test,y_train=y_train,y_test=y_test)

print(r_score)
print(a_score)


[2023-09-25 05:05:40,909 - Risk Analysis - INFO - directory is created ]
[2023-09-25 05:05:40,909 - Risk Analysis - INFO - directory is created ]


0:	learn: 0.6379896	total: 207ms	remaining: 20.5s
1:	learn: 0.5932447	total: 266ms	remaining: 13s
2:	learn: 0.5561812	total: 336ms	remaining: 10.9s
3:	learn: 0.5256393	total: 398ms	remaining: 9.56s
4:	learn: 0.4995769	total: 543ms	remaining: 10.3s
5:	learn: 0.4771033	total: 653ms	remaining: 10.2s
6:	learn: 0.4582603	total: 719ms	remaining: 9.55s
7:	learn: 0.4419565	total: 794ms	remaining: 9.13s
8:	learn: 0.4275244	total: 866ms	remaining: 8.76s
9:	learn: 0.4155437	total: 929ms	remaining: 8.36s
10:	learn: 0.4046969	total: 993ms	remaining: 8.03s
11:	learn: 0.3954985	total: 1.07s	remaining: 7.83s
12:	learn: 0.3872981	total: 1.12s	remaining: 7.52s
13:	learn: 0.3800366	total: 1.18s	remaining: 7.25s
14:	learn: 0.3741283	total: 1.24s	remaining: 7s
15:	learn: 0.3686820	total: 1.29s	remaining: 6.78s
16:	learn: 0.3643239	total: 1.37s	remaining: 6.71s
17:	learn: 0.3606899	total: 1.43s	remaining: 6.51s
18:	learn: 0.3566136	total: 1.49s	remaining: 6.35s
19:	learn: 0.3534903	total: 1.55s	remaining: 6